In [1]:
import re
import sqlite3
import pandas as pd
import numpy as np
import joblib

#For Flask
from flask import Flask, jsonify

In [2]:
#Import library for tokeize, stemming, and stopwords
import nltk
from nltk import word_tokenize
nltk.download('punkt')
nltk.download('stopwords')
from nltk.corpus import stopwords as stopwords_scratch

#Import library for sklearn model sentiment analysis
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import f1_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import PredefinedSplit
from sklearn.model_selection import train_test_split

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\rahad\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\rahad\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
# Import library for Tensorflow Model Sentiment Analysis
from keras import optimizers
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import LSTM,Dense
from keras.layers import Embedding
from keras.callbacks import EarlyStopping
from tensorflow import keras
from keras.models import load_model

In [4]:
# Import library for Flask
from flask import Flask, request, jsonify,render_template
from flasgger import Swagger, LazyString, LazyJSONEncoder, swag_from
# !pip install unidecode
from unidecode import unidecode

In [ ]:
#Swagger UI Definition
app = Flask(__name__)

app.json_encoder = LazyJSONEncoder
swagger_template = dict(
info = {
    'title' : LazyString(lambda: 'Sental (Sentiment Analysis)'),
    'version' : LazyString(lambda : '1.0.0'),
    'description': LazyString(lambda : 'Data menganalisa suatu sentiment'),
},
    host = LazyString(lambda: request.host)
)

swagger_config = {
    'headers': [],
    'specs': [
        {
        'endpoint': 'docs',
        'route': '/docs.json',
        }
    ],
    'static_url_path': '/flasgger_static',
    'swagger_ui': True,
    'specs_route': '/docs/'
}
swagger = Swagger(app, template=swagger_template,
                 config = swagger_config)

#Connect db and csv
conn = sqlite3.connect('data/output.db', check_same_thread=False)
df_alay = pd.read_csv('data/new_kamusalay.csv', names=['alay', 'cleaned'], encoding= 'latin-1')
df_raw = pd.read_csv('data/train_preprocess.tsv', sep='\t', names=['Text', 'Sentiment'])
df_raw.drop_duplicates()

#Define and execute query for unexistence data tables
#Tables will contain fields with dirty text (text & file) and cleaned text (text & file)
conn.execute('''CREATE TABLE IF NOT EXISTS data_text_sk (text_id INTEGER PRIMARY KEY AUTOINCREMENT, Text varchar(255), Sentiment varchar(255));''')
conn.execute('''CREATE TABLE IF NOT EXISTS data_file_sk (text_id INTEGER PRIMARY KEY AUTOINCREMENT, Text varchar(255), Sentiment varchar(255));''')
conn.execute('''CREATE TABLE IF NOT EXISTS data_text_tf (text_id INTEGER PRIMARY KEY AUTOINCREMENT, Text varchar(255), Sentiment varchar(255));''')
conn.execute('''CREATE TABLE IF NOT EXISTS data_file_tf (text_id INTEGER PRIMARY KEY AUTOINCREMENT, Text varchar(255), Sentiment varchar(255));''')

list_stopwords = stopwords_scratch.words('indonesian')
list_stopwords_en = stopwords_scratch.words('english')
list_stopwords.extend(list_stopwords_en)
list_stopwords.extend(['ya', 'yg', 'ga', 'yuk', 'dah', 'baiknya', 'berkali', 'kali', 'kurangnya', 'mata', 'olah', 'sekurang', 'setidak', 'tama', 'tidaknya'])

#Add External Stopwords
f = open("stopwords/tala-stopwords-indonesia.txt", "r")
stopword_external = []
for line in f:
    stripped_line = line.strip()
    line_list = stripped_line.split()
    stopword_external.append(line_list[0])
f.close()
list_stopwords.extend(stopword_external)
stopwords = list_stopwords

#Creating function for Cleansing Process
def lowercase(text): # Change uppercase characters to lowercase
    return text.lower()
def special(text):
    text = re.sub(r'\W', ' ', str(text), flags=re.MULTILINE)
    return text
def single(text):
    text = re.sub(r'\s+[a-zA-Z]\s+', ' ', text, flags=re.MULTILINE)
    return text
def singlestart(text):
    text = re.sub(r'\^[a-zA-Z]\s+', ' ', text, flags=re.MULTILINE)
    return text
def mulspace(text):
    text = re.sub(r'\s+', ' ', text, flags=re.MULTILINE)
    return text
def rt(text):#Removing RT
    text = re.sub(r'rt @\w+: ', ' ', text, flags=re.MULTILINE)
    return text
def prefixedb(text):#Removing prefixed 'b'
    text = re.sub(r'^b\s+', '', text, flags=re.MULTILINE)
    return text
def misc(text):
    text = re.sub(r'((www\.[^\s]+)|(https?://[^\s]+)|(http?://[^\s]+))|([#@]\S+)|user|\n|\t', ' ', text, flags=re.MULTILINE)
    return text

#Mapping for kamusalay
alay_mapping = dict(zip(df_alay['alay'], df_alay['cleaned']))
def alay(text):
    wordlist = text.split()
    text_alay = [alay_mapping.get(x,x) for x in wordlist]
    clean_alay = ' '.join(text_alay)
    return clean_alay

def stopwrds(text): 
    text_tokens = word_tokenize(text)
    tokens_without_sw = [word for word in text_tokens if not word in stopwords]
    output_sw = ' '.join(tokens_without_sw)
    return output_sw

#Function for text cleansing
def cleansing(text):
    text = lowercase(text)
    text = special(text)
    text = single(text)
    text = singlestart(text)
    text = mulspace(text)
    text = rt(text)
    text = prefixedb(text)
    text = misc(text)
    text = alay(text)
    # text = stopwrds(text)
    return text

#Sklearn Neural Network Analysis Sentiment
#Load the sklearn Model
# f1 = joblib.load('data/score.pkl')
model_NN = joblib.load(r"C:\Users\rahad\OneDrive\Documents\Binar Machine Learning - Platinum\Platinum Binar Academy_R1\data\MLPCPlatinumTfidf0.88%.pkl")
# vectorizer = joblib.load('data/vectorizer.pkl')

#Function for CSV Sklearn Analysis
def sentiment_csv_nn(input_file):
    column = input_file.iloc[:, 0]
    print(column)
    
    #Define and execute query for insert cleaned text and sentiment to sqlite database
    for data_file in column:
        data_clean = cleansing(data_file)
        sent = model_NN.predict(pd.DataFrame([data_clean])[0])[0]
        # sent = 'Positive' if sent == 2 else 'Neutral' if sent ==1 else 'Negative' if sent ==0 else 'None'
        query = "insert into data_file_sk ('Text', 'Sentiment') values (?, ?)"
        val = (data_clean,str(sent))
        conn.execute(query, val)
        conn.commit()
        print(data_file)

#Create Homepage
@swag_from(r"C:\Users\rahad\Downloads\Platinum Binar Academy\docs\welcome_pages.yml", methods=['GET'])
@app.route('/', methods=['GET'])
def get():
    return "Welcome to Sental Dashboard"

#Text Analysis Sklearn
#Input text to analyze
@swag_from(r"C:\Users\rahad\Downloads\Platinum Binar Academy\docs\text_sklearn.yml", methods=['POST'])
@app.route('/text_sklearn', methods=['POST'])
def text_sentiment_sklearn():
    #Get text from user
    input_text = str(request.form['text'])
    
    #Cleaning text
    output_text = cleansing(input_text)
    
    #Model Prediction for Sentiment Analysis
    sent = model_NN.predict(pd.DataFrame([output_text])[0])[0]
    # sent = 'Positive' if sent == 2 else 'Neutral' if sent ==1 else 'Negative' if sent ==0 else 'None'
    
    # Define and execute query for insert cleaned text and sentiment to sqlite database
    query = "insert into data_text_sk (text,sentiment) values (?, ?)"
    val = (output_text,str(sent))
    conn.execute(query, val)
    conn.commit()
    
    #Define API Response
    json_response = {
        'description': "Analysis Sentiment Success!",
        'F1 on test set': "MLP Classifier with Tfidf",
        'text' : output_text,
        'sentiment' : str(sent)
    }
    response_data = jsonify(json_response)
    return response_data

#Endpoint for File Analysis SKLearn
@swag_from(r"C:\Users\rahad\Downloads\Platinum Binar Academy\docs\file_sklearn.yml", methods=['POST'])
@app.route('/file_sklearn', methods=['POST'])
def file_sentiment_sk():
    #Get File
    file = request.files['file']
    try:
            datacsv = pd.read_csv(file, encoding='iso-8859-1')
    except:
            datacsv = pd.read_csv(file, encoding='utf-8')
    
    #Cleaning file
    sentiment_csv_nn(datacsv)
    
    #Define API response
    select_data = conn.execute("SELECT * FROM data_file_sk")
    conn.commit
    data = [
        dict(text_id=row[0], text=row[1], sentiment=row[2])
    for row in select_data.fetchall()
    ]
    
    return jsonify(data)

#Tensorflow LSTM Model Analysis Sentimen
#Load the Tensorflow Model
model = load_model(r"C:\Users\rahad\Downloads\Platinum Binar Academy\data\LSTM_Binar_model.h5")
tokenizer = joblib.load(r"C:\Users\rahad\Downloads\Platinum Binar Academy\data\tokenizer.pickle")

#Model Prediction
#Create Function for Sentiment Prediction
def predict_sentiment(text):
    sentiment_tf = ['negative', 'neutral', 'positive']
    text = cleansing(text)
    tw = tokenizer.texts_to_sequences([text])
    tw = pad_sequences(tw, maxlen=96)
    prediction = model.predict(tw)
    polarity = np.argmax(prediction[0])
    return sentiment_tf[polarity]

def sentiment_csv_tf(input_file):
    column = input_file.iloc[:, 0]
    print(column)
    
    # Define and execute query for insert cleaned text and sentiment to sqlite database
    for data_file in column:
        data_clean = cleansing(data_file)
        sent = predict_sentiment(data_clean)
        query = "insert into data_file_tf ('Text', 'Sentiment') values (?, ?)"
        val = (data_clean,sent)
        conn.execute(query, val)
        conn.commit()
        print(data_file)

#Endpoint for Text Analysis Tensorflow
#Input text to analyze
@swag_from(r"C:\Users\rahad\Downloads\Platinum Binar Academy\docs\text_tensorflow.yml", methods=['POST'])
@app.route('/text_tensorflow', methods=['POST'])
def text_sentiment_tf():
    #Get text from user
    input_text = str(request.form['text'])
    
    #Cleansing text
    output_text = cleansing(input_text)
    
    #Model Prediction for Sentiment Analysis
    output_sent = predict_sentiment(output_text)
    
    #Define and execute query for insert cleaned text and sentiment to sqlite database
    query = "insert into data_text_tf (Text,Sentiment) values (?, ?)"
    val = (output_text,output_sent)
    conn.execute(query, val)
    conn.commit()
    
    #Define API response
    json_response = {
        'description': "Analysis Sentiment Success!",
        'text' : output_text,
        'sentiment' : output_sent
    }
    response_data = jsonify(json_response)
    return response_data

#Endpoint for File Analysis Tensorflow
@swag_from(r"C:\Users\rahad\Downloads\Platinum Binar Academy\docs\file_tensorflow.yml", methods=['POST'])
@app.route('/file_tensorflow', methods=['POST'])
def file_sentiment_tf():
    #Get file
    file = request.files['file']
    try:
            datacsv = pd.read_csv(file, encoding='iso-8859-1')
    except:
            datacsv = pd.read_csv(file, encoding='utf-8')
    
    #Cleaning file
    sentiment_csv_tf(datacsv)
    
    #Define API response
    select_data = conn.execute("SELECT * FROM data_file_tf")
    conn.commit
    data = [
        dict(text_id=row[0], text=row[1], sentiment=row[2])
    for row in select_data.fetchall()
    ]
    
    return jsonify(data)

    

if __name__ == '__main__':
    app.run()

C:\Users\rahad\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:288: UserWarning: Trying to unpickle estimator TfidfTransformer from version 1.0.2 when using version 1.2.0. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
C:\Users\rahad\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:288: UserWarning: Trying to unpickle estimator TfidfVectorizer from version 1.0.2 when using version 1.2.0. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
C:\Users\rahad\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:288: UserWarning: Trying to unpickle estimator MLPClassifier from version 1.0.2 when using version 1.2.0. This might lead 

 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:5000 (Press CTRL+C to quit)
127.0.0.1 - - [10/Mar/2023 21:40:07] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [10/Mar/2023 21:40:13] "GET /docs/ HTTP/1.1" 200 -
127.0.0.1 - - [10/Mar/2023 21:40:14] "GET /flasgger_static/swagger-ui.css HTTP/1.1" 304 -
127.0.0.1 - - [10/Mar/2023 21:40:14] "GET /flasgger_static/lib/jquery.min.js HTTP/1.1" 304 -
127.0.0.1 - - [10/Mar/2023 21:40:15] "GET /flasgger_static/swagger-ui-standalone-preset.js HTTP/1.1" 304 -
127.0.0.1 - - [10/Mar/2023 21:40:15] "GET /flasgger_static/swagger-ui-bundle.js HTTP/1.1" 304 -
127.0.0.1 - - [10/Mar/2023 21:40:15] "GET /docs.json HTTP/1.1" 200 -


0                             menyesal sudah buka hati .
1      buang saja pak , uu kok bikin kebal sendiri . ...
2      gue sejujur nya masih kecewa sama drama are ka...
3      adik saya sedang menonton harry potter di tran...
4      saya sering pergi ke kampung daun setiap kali ...
                             ...                        
995    bersama keluarga betapa menyenangkan jika maka...
996    salah satu yang terbaik untuk tempat makanan c...
997    bagaimana indonesia bisa maju ? mau aja lo sem...
998    kalau boleh jujur , aku agak kecewa sama keput...
999    saya pernah mencicipi berbagai soto di beberap...
Name: Tweet, Length: 1000, dtype: object
menyesal sudah buka hati .
buang saja pak , uu kok bikin kebal sendiri . kalau fh nyinyir biarkan saja .
gue sejujur nya masih kecewa sama drama are kamu human to . pertama , main chara perempuan nya apa banget . kedua , tidak ada latar belakang yang jelas kenapa younghoon sangat turut banget sama human nam shin . ketiga , nam shi

sate nya besar-besar . bumbu nya dipisah . dikasih irisan bawang merah dan cabe rawit dikukus , porsi lontong sama nasi nya juga pas . pokok nya saya suka .
sistem pelayanan di cost telah berubah menjadi sistem mandiri sel - pelayanan . harga makanan juga mengalamai kenaikan dengan porsi yang sama besar . walau harga tetap oke dan tidak dikategorikan mahal , namun kepuasan secra rata-rata yang saya terima menurun dibanding sebelum sistem berubah .
adit kayak tarik
di balik munculnya banyak restoran itali di bandung , pizza hut masih merupakan salah satu alternatif restoran pizza terbaik menurut ku . sesekali masih bisa merindukan pizza yang terdapat di sini . apalagi , sering ada menu seasonal yang membuat kita semakin tergoda . selain menu seasonal , pizza keju dan tuna nya selalu masuk ke daftar pesanan ku !
saya penerima minimal , saya yang memesan barang nya .
kenapa roti nya saya robek-robek ? karena keras banget . hotel bintang 4 tapi fasilitas pelayanan nya mengecewakan
kafe res

...

1/1 [==============================] - 0s 31ms/step
lokasi nya cukup tersembunyi daerah maribaya - lembang , tapi asik buat nongkrong sambil menikmati udara dingin lembang . tempat ini sejenis kafe untuk kelas menengah ke atas . untuk pasangan yang berpacaran , tempat ini romantis buat makan malam . menu makanan bervariasi kok , ada steak , pizza , sop buntut , dessert , dll. harga menengah ke atas , tapi masih terjangkau .
1/1 [==============================] - 0s 12ms/step
saya agak kecewa dengan pelayanan yang diberikan hotel berry biz . kemarin saya menginap di hotel itu di daerah bali , lalu ketika saya meminta tolong untuk meminjam haridryer , mereka tidak berikan dengan alasan tidak . menurut saya harus nya disiapkan untuk alat-alat seperti itu .
1/1 [==============================] - 0s 17ms/step
eh kompas suku asmat mana berita nya ? yang tidak penting lu memberitakan . lu ini media berita apa tim hore sih ?
1/1 [==============================] - 0s 19ms/step
bosan , muak , lu

1/1 [==============================] - 0s 16ms/step
nah ini dia warung makan yang cocok buat aku kalau ke bandung . dengan menu lokal tetapi dilengkapi dengan sambal pedas walau tidak terlalu pedas . yang menarik , bangunan nya , lalu lokasi juga . menu nya pas bagi yang senang kuliner lokal rasa nasional . bagi yang ke bandung . jangan lewatkan warung makan ampera , terutama yang di jalan pelajar pejuang . dijamin mantap .
1/1 [==============================] - 0s 18ms/step
sangat cocok untuk anda yang kelaparan di tengah malam setelah seharian berwisata di kota bandung dan mencari sekedar makanan pengganjal perut
1/1 [==============================] - 0s 16ms/step
suasana di kuis butcher jalan riau menyenangkan karena ada ruang terbuka nya , sehingga kita bisa makan sambil menikmati suasana kota bandung . lokasi nya sangat strategis di jalan riau dekat dengan fo dan pusat perbelanjaan lain di bandung . steak nya mengenyangkan , porsi nya cukup besar . saus nya standar , mash potato h

enak pizza nya , bir nya juga banyak varian , yang jarang ditemui ada di sana , enak buat santai-santai sama teman , berdua sama pacar juga enak . hehe
1/1 [==============================] - 0s 19ms/step
maaf pol cuma berani dengan ahok . dengan brizik sudah tak sudah dipanggil 3 kali tidak hadir sudah jadi dpo kok tidak berani ciduk . 243 juta rakyat ind dukung jokahok . tuntaskan sara ceng dan yang bayarin demonstrasi-demonstrasi fpi untuk fitnah amp ; provokasi sara jokahok . korban fitnah buni fpi mui byrn say wo2 ht penulis
1/1 [==============================] - 0s 19ms/step
bank bca di pgc payah sekali pelayanan nya . jadi menyesal dah jadi nasabah nya kalau begini cara nya
1/1 [==============================] - 0s 18ms/step
biasa-biasa saja tidak ada yang spesial , ayam goreng nya terlalu berminyak , makanan semua dingin cuma nasi nya yang panas , harga nya normal .
1/1 [==============================] - 0s 21ms/step
kalau makanan kembali lagi ke selera masing-masing . menurut p

1/1 [==============================] - 0s 15ms/step
beragam menu bakso tahu dan berbagai menu minuman yang beragam membuat raja bakso tahu saboga saya rekomendasikan bumbu kacang yang manis dan pedas juga enak
1/1 [==============================] - 0s 19ms/step
rumah payung terkenal dengan restoran yang selain menyajikan pemandangan khas dago pakar resort , live musik , juga makanan yang enak . mereka punya bebek peking yang enak , gurame gurih , sate maranggi yang enak dan steak khas rumah payung yang harus anda coba . saya merekomendasikan minuman sehat nona hijau . enak , segar dam sehat ! selain resto , rumah payung juga memiliki penginapan .
1/1 [==============================] - 0s 23ms/step
tolong dibaca pesan saya ! di dalam kotak handphone tidak ada kartu garansi bbm . ini penipuan ya ?
1/1 [==============================] - 0s 19ms/step
saya sangat puas dengan spesifikasi laptop asus
1/1 [==============================] - 0s 21ms/step
makanan menurut saya biasa saja , hanya s

127.0.0.1 - - [10/Mar/2023 22:16:21] "POST /file_tensorflow HTTP/1.1" 200 -
